In [387]:
import numpy as np
import pandas as pd
from ydata_profiling import ProfileReport
import tensorflow as tf
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import TruncatedSVD
from scipy.sparse import csr_matrix
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, Flatten, Dense, Concatenate, Dropout
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.models import Model
from surprise import Dataset, Reader
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import silhouette_score, mean_absolute_error, mean_squared_error, r2_score 
from sklearn.model_selection import train_test_split
from sklearn.metrics.pairwise import cosine_similarity
import warnings
warnings.filterwarnings('ignore')
df_book = pd.read_csv("reccomendersystems/Books.csv")
df_raiting = pd.read_csv("reccomendersystems/Ratings.csv")
df_user = pd.read_csv("reccomendersystems/Users.csv")

In [388]:
df_book.head()

df_books = df_book[["ISBN","Book-Title","Book-Author","Year-Of-Publication","Publisher"]]	

In [389]:
df_raiting.head()

df_raiting.isna().sum()

User-ID        0
ISBN           0
Book-Rating    0
dtype: int64

In [390]:
df_user.head()

df_user.isna().sum()

df_user = df_user[["User-ID","Location"]]

In [391]:
#Significant portion of the df, drop age? 

df_user.shape

(278858, 2)

In [392]:
df_raiting.head()

User-ID        ISBN  Book-Rating
0   276725  034545104X            0
1   276726  0155061224            5
2   276727  0446520802            0
3   276729  052165615X            3
4   276729  0521795028            6

In [393]:
df_raiting.shape

(1149780, 3)

In [394]:
# Join df_user and df_rating on "User-ID"
df_user_rating = pd.merge(df_user, df_raiting, on="User-ID", how="inner")

# Join the merged df_user_rating with df_books on "ISBN"
final_df = pd.merge(df_user_rating, df_books, on="ISBN", how="inner")


final_df.head()

User-ID                   Location        ISBN  Book-Rating  \
0        2  stockton, california, usa  0195153448            0   
1        8   timmins, ontario, canada  0002005018            5   
2    11400    ottawa, ontario, canada  0002005018            0   
3    11676              n/a, n/a, n/a  0002005018            8   
4    41385   sudbury, ontario, canada  0002005018            0   

            Book-Title           Book-Author Year-Of-Publication  \
0  Classical Mythology    Mark P. O. Morford                2002   
1         Clara Callan  Richard Bruce Wright                2001   
2         Clara Callan  Richard Bruce Wright                2001   
3         Clara Callan  Richard Bruce Wright                2001   
4         Clara Callan  Richard Bruce Wright                2001   

                 Publisher  
0  Oxford University Press  
1    HarperFlamingo Canada  
2    HarperFlamingo Canada  
3    HarperFlamingo Canada  
4    HarperFlamingo Canada

In [395]:
final_df["Book-Rating"].value_counts()

Book-Rating
0     647294
8      91804
10     71225
7      66402
9      60778
5      45355
6      31687
4       7617
3       5118
2       2375
1       1481
Name: count, dtype: int64

In [396]:
final_df_non_zero = final_df.loc[final_df['Book-Rating'] != 0]

In [397]:
final_df_non_zero.isnull().any()

User-ID                False
Location               False
ISBN                   False
Book-Rating            False
Book-Title             False
Book-Author             True
Year-Of-Publication    False
Publisher               True
dtype: bool

In [398]:
final_df_non_zero.dropna()


User-ID                   Location        ISBN  Book-Rating  \
1              8   timmins, ontario, canada  0002005018            5   
3          11676              n/a, n/a, n/a  0002005018            8   
5          67544   toronto, ontario, canada  0002005018            8   
8         116866                  ottawa, ,  0002005018            9   
9         123629  kingston, ontario, canada  0002005018            9   
...          ...                        ...         ...          ...   
1031130   278851         dallas, texas, usa  067161746X            7   
1031132   278851         dallas, texas, usa  0767907566            5   
1031133   278851         dallas, texas, usa  0884159221            7   
1031134   278851         dallas, texas, usa  0912333022            7   
1031135   278851         dallas, texas, usa  1569661057           10   

                                                Book-Title  \
1                                             Clara Callan   
3                                             Clara Callan   
5                                             Clara Callan   
8                                             Clara Callan   
9                                             Clara Callan   
...                                                    ...   
1031130  The Bachelor Home Companion: A Practical Guide...   
1031132  All Elevations Unknown: An Adventure in the He...   
1031133  Why stop?: A guide to Texas historical roadsid...   
1031134  The Are You Being Served? Stories: 'Camping In...   
1031135  Dallas Street Map Guide and Directory, 2000 Ed...   

                  Book-Author Year-Of-Publication                 Publisher  
1        Richard Bruce Wright                2001     HarperFlamingo Canada  
3        Richard Bruce Wright                2001     HarperFlamingo Canada  
5        Richard Bruce Wright                2001     HarperFlamingo Canada  
8        Richard Bruce Wright                2001     HarperFlamingo Canada  
9        Richard Bruce Wright                2001     HarperFlamingo Canada  
...                       ...                 ...                       ...  
1031130         P.J. O'Rourke                1987              Pocket Books  
1031132          Sam Lightner                2001            Broadway Books  
1031133         Claude Dooley                1985           Lone Star Books  
1031134          Jeremy Lloyd                1997                Kqed Books  
1031135                Mapsco                1999  American Map Corporation  

[383838 rows x 8 columns]

In [399]:
report = ProfileReport(final_df_non_zero)
report


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [400]:
final_df_non_zero['Location'] = final_df_non_zero['Location'].str.split(',').str[-1].str.strip()


In [401]:
final_df_non_zero.head()

User-ID Location        ISBN  Book-Rating    Book-Title  \
1        8   canada  0002005018            5  Clara Callan   
3    11676      n/a  0002005018            8  Clara Callan   
5    67544   canada  0002005018            8  Clara Callan   
8   116866           0002005018            9  Clara Callan   
9   123629   canada  0002005018            9  Clara Callan   

            Book-Author Year-Of-Publication              Publisher  
1  Richard Bruce Wright                2001  HarperFlamingo Canada  
3  Richard Bruce Wright                2001  HarperFlamingo Canada  
5  Richard Bruce Wright                2001  HarperFlamingo Canada  
8  Richard Bruce Wright                2001  HarperFlamingo Canada  
9  Richard Bruce Wright                2001  HarperFlamingo Canada

In [402]:
final_df_non_zero["Location"].isnull().sum()

0

In [403]:
specific_value = final_df_non_zero.loc[8, 'Location']
print(type(specific_value))


<class 'str'>


In [404]:
final_df_non_zero['Location'] = final_df_non_zero['Location'].str.strip()

In [405]:
specific_value = final_df_non_zero.loc[8, 'Location']
print(specific_value)

In [406]:
final_df_non_zero = final_df_non_zero[final_df_non_zero['Location'].str.strip() != '']

In [407]:
final_df_non_zero.head()

User-ID Location        ISBN  Book-Rating    Book-Title  \
1         8   canada  0002005018            5  Clara Callan   
3     11676      n/a  0002005018            8  Clara Callan   
5     67544   canada  0002005018            8  Clara Callan   
9    123629   canada  0002005018            9  Clara Callan   
11   200273   canada  0002005018            8  Clara Callan   

             Book-Author Year-Of-Publication              Publisher  
1   Richard Bruce Wright                2001  HarperFlamingo Canada  
3   Richard Bruce Wright                2001  HarperFlamingo Canada  
5   Richard Bruce Wright                2001  HarperFlamingo Canada  
9   Richard Bruce Wright                2001  HarperFlamingo Canada  
11  Richard Bruce Wright                2001  HarperFlamingo Canada

In [408]:
df_final = final_df_non_zero[final_df_non_zero['Location'] != "n/a"]

In [409]:
df_final.head()

User-ID Location        ISBN  Book-Rating    Book-Title  \
1         8   canada  0002005018            5  Clara Callan   
5     67544   canada  0002005018            8  Clara Callan   
9    123629   canada  0002005018            9  Clara Callan   
11   200273   canada  0002005018            8  Clara Callan   
12   210926   canada  0002005018            9  Clara Callan   

             Book-Author Year-Of-Publication              Publisher  
1   Richard Bruce Wright                2001  HarperFlamingo Canada  
5   Richard Bruce Wright                2001  HarperFlamingo Canada  
9   Richard Bruce Wright                2001  HarperFlamingo Canada  
11  Richard Bruce Wright                2001  HarperFlamingo Canada  
12  Richard Bruce Wright                2001  HarperFlamingo Canada

In [410]:
df_final.reset_index(drop=True, inplace=True)

In [411]:
df_final.head()

User-ID Location        ISBN  Book-Rating    Book-Title  \
0        8   canada  0002005018            5  Clara Callan   
1    67544   canada  0002005018            8  Clara Callan   
2   123629   canada  0002005018            9  Clara Callan   
3   200273   canada  0002005018            8  Clara Callan   
4   210926   canada  0002005018            9  Clara Callan   

            Book-Author Year-Of-Publication              Publisher  
0  Richard Bruce Wright                2001  HarperFlamingo Canada  
1  Richard Bruce Wright                2001  HarperFlamingo Canada  
2  Richard Bruce Wright                2001  HarperFlamingo Canada  
3  Richard Bruce Wright                2001  HarperFlamingo Canada  
4  Richard Bruce Wright                2001  HarperFlamingo Canada

In [412]:
# Identify non-numeric values
non_numeric_values = df_final[~df_final['Book-Rating'].astype(str).str.isdigit()]['Book-Rating']

# Check unique non-numeric values
print(non_numeric_values.unique())

[]


In [413]:
avg_rating_df = df_final.groupby('Book-Title')['Book-Rating'].mean().reset_index()

# Rename the 'Book-Rating' column to 'avg_ratings' in the resulting DataFrame
avg_rating_df.rename(columns={'Book-Rating': 'avg_ratings'}, inplace=True)

# Display the first 10 rows to verify
avg_rating_df.head(10)

Book-Title  avg_ratings
0   A Light in the Storm: The Civil War Diary of ...     9.000000
1   Ask Lily (Young Women of Faith: Lily Series, ...     8.000000
2                                       Dark Justice    10.000000
3   Earth Prayers From around the World: 365 Pray...     7.142857
4   Final Fantasy Anthology: Official Strategy Gu...    10.000000
5   Flight of Fancy: American Heiresses (Zebra Ba...     8.000000
6   Garfield Bigger and Better (Garfield (Numbere...     7.000000
7                          God's Little Promise Book     9.000000
8   Good Wives: Image and Reality in the Lives of...     8.000000
9   Goosebumps Monster Edition 1: Welcome to Dead...     6.666667

In [414]:
num_rating_df = df_final.groupby('Book-Title').count()['Book-Rating'].reset_index()
num_rating_df.rename(columns={'Book-Rating': 'num_ratings'}, inplace=True)
num_rating_df.head(10)

Book-Title  num_ratings
0   A Light in the Storm: The Civil War Diary of ...            1
1   Ask Lily (Young Women of Faith: Lily Series, ...            1
2                                       Dark Justice            1
3   Earth Prayers From around the World: 365 Pray...            7
4   Final Fantasy Anthology: Official Strategy Gu...            2
5   Flight of Fancy: American Heiresses (Zebra Ba...            1
6   Garfield Bigger and Better (Garfield (Numbere...            1
7                          God's Little Promise Book            1
8   Good Wives: Image and Reality in the Lives of...            4
9   Goosebumps Monster Edition 1: Welcome to Dead...            3

In [415]:
ninki_df = num_rating_df.merge(avg_rating_df, on='Book-Title')
ninki_df.head(10)

Book-Title  num_ratings  avg_ratings
0   A Light in the Storm: The Civil War Diary of ...            1     9.000000
1   Ask Lily (Young Women of Faith: Lily Series, ...            1     8.000000
2                                       Dark Justice            1    10.000000
3   Earth Prayers From around the World: 365 Pray...            7     7.142857
4   Final Fantasy Anthology: Official Strategy Gu...            2    10.000000
5   Flight of Fancy: American Heiresses (Zebra Ba...            1     8.000000
6   Garfield Bigger and Better (Garfield (Numbere...            1     7.000000
7                          God's Little Promise Book            1     9.000000
8   Good Wives: Image and Reality in the Lives of...            4     8.000000
9   Goosebumps Monster Edition 1: Welcome to Dead...            3     6.666667

In [416]:
top_50 = ninki_df[ninki_df['num_ratings']>=250].sort_values("avg_ratings",ascending=False).head(50)
top_50.head()

Book-Title  num_ratings  \
44341   Harry Potter and the Prisoner of Azkaban (Book 3)          269   
120882                              To Kill a Mockingbird          257   
44351   Harry Potter and the Sorcerer's Stone (Harry P...          303   
44322    Harry Potter and the Chamber of Secrets (Book 2)          314   
113552                            The Secret Life of Bees          395   

        avg_ratings  
44341      9.052045  
120882     8.996109  
44351      8.920792  
44322      8.831210  
113552     8.488608

In [417]:
report_processed = ProfileReport(df_final)
report_processed


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [418]:
x = final_df.groupby('User-ID').count()['Book-Rating']>100
knowledgable_users = x[x].index

In [419]:
filtered_rating = final_df[final_df['User-ID'].isin(knowledgable_users)]

In [420]:
y = filtered_rating.groupby('Book-Title').count()['Book-Rating']>=50
famous_books = y[y].index

In [421]:
final_ratings =  filtered_rating[filtered_rating['Book-Title'].isin(famous_books)]

In [422]:
final_ratings.head()

User-ID                      Location        ISBN  Book-Rating  \
31    11676                 n/a, n/a, n/a  0399135782            9   
32    29526     knoxville, tennessee, usa  0399135782            9   
33    36836  raleigh, north carolina, usa  0399135782            0   
34    46398       san antonio, texas, usa  0399135782            9   
38   113270       evanston, illinois, usa  0399135782            0   

                Book-Title Book-Author Year-Of-Publication         Publisher  
31  The Kitchen God's Wife     Amy Tan                1991  Putnam Pub Group  
32  The Kitchen God's Wife     Amy Tan                1991  Putnam Pub Group  
33  The Kitchen God's Wife     Amy Tan                1991  Putnam Pub Group  
34  The Kitchen God's Wife     Amy Tan                1991  Putnam Pub Group  
38  The Kitchen God's Wife     Amy Tan                1991  Putnam Pub Group

In [423]:
sparse_matrix = final_ratings.pivot_table(index='Book-Title',columns='User-ID'
                          ,values='Book-Rating')
sparse_matrix

User-ID                                             254     507     882     \
Book-Title                                                                   
1984                                                   9.0     NaN     NaN   
1st to Die: A Novel                                    NaN     0.0     NaN   
2010: Odyssey Two                                      NaN     NaN     NaN   
204 Rosewood Lane                                      NaN     NaN     NaN   
24 Hours                                               NaN     NaN     NaN   
...                                                    ...     ...     ...   
Year of Wonders                                        NaN     NaN     NaN   
You Belong To Me                                       NaN     NaN     NaN   
Zen and the Art of Motorcycle Maintenance: An I...     NaN     NaN     NaN   
Zoya                                                   NaN     NaN     NaN   
\O\" Is for Outlaw"                                    NaN     NaN     NaN   

User-ID                                             1424    1435    1733    \
Book-Title                                                                   
1984                                                   NaN     NaN     NaN   
1st to Die: A Novel                                    NaN     NaN     NaN   
2010: Odyssey Two                                      NaN     NaN     NaN   
204 Rosewood Lane                                      NaN     NaN     NaN   
24 Hours                                               NaN     NaN     NaN   
...                                                    ...     ...     ...   
Year of Wonders                                        7.0     NaN     NaN   
You Belong To Me                                       NaN     NaN     NaN   
Zen and the Art of Motorcycle Maintenance: An I...     NaN     NaN     NaN   
Zoya                                                   NaN     NaN     NaN   
\O\" Is for Outlaw"                                    NaN     NaN     NaN   

User-ID                                             1903    2033    2110    \
Book-Title                                                                   
1984                                                   NaN     NaN     NaN   
1st to Die: A Novel                                    NaN     NaN     NaN   
2010: Odyssey Two                                      NaN     NaN     NaN   
204 Rosewood Lane                                      NaN     NaN     NaN   
24 Hours                                               NaN     NaN     NaN   
...                                                    ...     ...     ...   
Year of Wonders                                        NaN     NaN     NaN   
You Belong To Me                                       NaN     NaN     NaN   
Zen and the Art of Motorcycle Maintenance: An I...     NaN     NaN     NaN   
Zoya                                                   NaN     NaN     NaN   
\O\" Is for Outlaw"                                    NaN     0.0     NaN   

User-ID                                             2276    ...  275020  \
Book-Title                                                  ...           
1984                                                   NaN  ...     NaN   
1st to Die: A Novel                                    NaN  ...     NaN   
2010: Odyssey Two                                      0.0  ...     NaN   
204 Rosewood Lane                                      NaN  ...     NaN   
24 Hours                                               NaN  ...     NaN   
...                                                    ...  ...     ...   
Year of Wonders                                        NaN  ...     NaN   
You Belong To Me                                       NaN  ...     NaN   
Zen and the Art of Motorcycle Maintenance: An I...     NaN  ...     NaN   
Zoya                                                   NaN  ...     NaN   
\O\" Is for Outlaw"                                    

In [424]:
sparse_matrix.fillna(0,inplace=True)
sparse_matrix

User-ID                                             254     507     882     \
Book-Title                                                                   
1984                                                   9.0     0.0     0.0   
1st to Die: A Novel                                    0.0     0.0     0.0   
2010: Odyssey Two                                      0.0     0.0     0.0   
204 Rosewood Lane                                      0.0     0.0     0.0   
24 Hours                                               0.0     0.0     0.0   
...                                                    ...     ...     ...   
Year of Wonders                                        0.0     0.0     0.0   
You Belong To Me                                       0.0     0.0     0.0   
Zen and the Art of Motorcycle Maintenance: An I...     0.0     0.0     0.0   
Zoya                                                   0.0     0.0     0.0   
\O\" Is for Outlaw"                                    0.0     0.0     0.0   

User-ID                                             1424    1435    1733    \
Book-Title                                                                   
1984                                                   0.0     0.0     0.0   
1st to Die: A Novel                                    0.0     0.0     0.0   
2010: Odyssey Two                                      0.0     0.0     0.0   
204 Rosewood Lane                                      0.0     0.0     0.0   
24 Hours                                               0.0     0.0     0.0   
...                                                    ...     ...     ...   
Year of Wonders                                        7.0     0.0     0.0   
You Belong To Me                                       0.0     0.0     0.0   
Zen and the Art of Motorcycle Maintenance: An I...     0.0     0.0     0.0   
Zoya                                                   0.0     0.0     0.0   
\O\" Is for Outlaw"                                    0.0     0.0     0.0   

User-ID                                             1903    2033    2110    \
Book-Title                                                                   
1984                                                   0.0     0.0     0.0   
1st to Die: A Novel                                    0.0     0.0     0.0   
2010: Odyssey Two                                      0.0     0.0     0.0   
204 Rosewood Lane                                      0.0     0.0     0.0   
24 Hours                                               0.0     0.0     0.0   
...                                                    ...     ...     ...   
Year of Wonders                                        0.0     0.0     0.0   
You Belong To Me                                       0.0     0.0     0.0   
Zen and the Art of Motorcycle Maintenance: An I...     0.0     0.0     0.0   
Zoya                                                   0.0     0.0     0.0   
\O\" Is for Outlaw"                                    0.0     0.0     0.0   

User-ID                                             2276    ...  275020  \
Book-Title                                                  ...           
1984                                                   0.0  ...     0.0   
1st to Die: A Novel                                    0.0  ...     0.0   
2010: Odyssey Two                                      0.0  ...     0.0   
204 Rosewood Lane                                      0.0  ...     0.0   
24 Hours                                               0.0  ...     0.0   
...                                                    ...  ...     ...   
Year of Wonders                                        0.0  ...     0.0   
You Belong To Me                                       0.0  ...     0.0   
Zen and the Art of Motorcycle Maintenance: An I...     0.0  ...     0.0   
Zoya                                                   0.0  ...     0.0   
\O\" Is for Outlaw"                                    

In [425]:
similarity_score = cosine_similarity(sparse_matrix)

In [426]:
similarity_score.shape

(1070, 1070)

In [439]:
import pandas as pd

def recommend(book_name):
    index = np.where(sparse_matrix.index == book_name)[0][0]
    similar_books = sorted(list(enumerate(similarity_score[index])), key=lambda x: x[1], reverse=True)[1:6]
    
    data = []
    for i in similar_books:
        item = []
        temp_df = df_books[df_books['Book-Title'] == sparse_matrix.index[i[0]]]
        book_titles = temp_df.drop_duplicates('Book-Title')['Book-Title'].values
        book_authors = temp_df.drop_duplicates('Book-Title')['Book-Author'].values
        for title, author in zip(book_titles, book_authors):
            item.append({'Book Title': title, 'Author': author})
        data.extend(item)
    
    # Convert the data list of dictionaries into a DataFrame
    recommended_books_cosine_df = pd.DataFrame(data)
    return recommended_books_cosine_df


In [443]:
cosine_reccomendation = recommend("1984")
cosine_reccomendation 

Book Title           Author
0                                        Animal Farm    George Orwell
1                                    Brave New World    Aldous Huxley
2  Slaughterhouse Five or the Children's Crusade:...    Kurt Vonnegut
3                                          Awakening      Kate Chopin
4                                The Handmaid's Tale  Margaret Atwood

In [429]:
from sklearn.decomposition import TruncatedSVD
import numpy as np
import matplotlib.pyplot as plt

svd = TruncatedSVD(n_components=sparse_matrix.shape[1] - 1)
svd.fit(sparse_matrix)

plt.figure(figsize=(10, 6))
plt.plot(np.cumsum(svd.explained_variance_ratio_))
plt.xlabel('Number of Components')
plt.ylabel('Cumulative Explained Variance')
plt.grid(True)
plt.show()
plt.savefig('explained_variance_sparse.png')
plt.close()  # Close the plot to free up memory

In [430]:
# this resulted in showing 500 components of explained varience 

In [431]:
from sklearn.decomposition import TruncatedSVD
from scipy.sparse import csr_matrix

# Convert the ratings matrix to a sparse CSR matrix
ratings_matrix_sparse = csr_matrix(sparse_matrix.values)

# Apply Truncated SVD
n_components = 500  # Number of latent factors to extract
svd = TruncatedSVD(n_components=n_components, random_state=42)
ratings_matrix_svd = svd.fit_transform(ratings_matrix_sparse)

# The output, ratings_matrix_svd, has shape [n_users, n_components]

In [432]:
# Filter df_books to include only titles present in sparse_matrix.index
df_books_aligned = df_books[df_books['Book-Title'].isin(sparse_matrix.index)].copy()

In [433]:
df_books_aligned.set_index('Book-Title', inplace=True)


In [434]:
def recommend_svd(book_name, similarity_scores, df_books_aligned, top_n=5):
    # # Standardize the book name to match the DataFrame indexing
    # book_name = book_name.lower().strip()

    # Check if the book is in the dataset
    if book_name not in df_books_aligned.index:
        return "Book not found in the dataset."

    # Find the index of the book
    index = np.where(df_books_aligned.index == book_name)[0][0]
    
    # Compute similarity scores for this book
    similar_books = sorted(list(enumerate(similarity_scores[index])), key=lambda x: x[1], reverse=True)[1:top_n+1]

    # Initialize a list to store recommended book details
    data = []

    # Fetch details of similar books
    for i in similar_books:
        idx = i[0]  # Index of the book in df_books_aligned
        book_title = df_books_aligned.index[idx]
        
        # Assuming df_books_aligned contains 'Book-Author' column
        book_author = df_books_aligned.loc[book_title, 'Book-Author'] if 'Book-Author' in df_books_aligned.columns else "Author Unknown"

        # Add book details to the list
        data.append((book_title, book_author))

    # Convert the list of tuples to a DataFrame for a nicer display
    recommended_books_df = pd.DataFrame(data, columns=['Book Title', 'Author'])

    return recommended_books_df


In [435]:
# Calculate cosine similarity for the SVD-transformed data
similarity_score_svd = cosine_similarity(ratings_matrix_svd)

In [444]:
book_name = "1984"  # Example book title
recommendation_svd = recommend_svd(book_name, similarity_score_svd, df_books_aligned, top_n=5)
recommendation_svd

Book Title  \
0                                   The Smoke Jumper   
1  Speaker for the Dead (Ender Wiggins Saga (Pape...   
2                       Suzanne's Diary for Nicholas   
3                                       Mirror Image   
4                                  I Is for Innocent   

                                              Author  
0  Book-Title
The Smoke Jumper    Nicholas Evans
...  
1  Book-Title
Speaker for the Dead (Ender Wiggins...  
2  Book-Title
Suzanne's Diary for Nicholas    Jam...  
3  Book-Title
Mirror Image    Danielle Steel
Mirr...  
4                                        Sue Grafton

In [448]:
def final_reccomended(df1, df2, df1top_n=3, df2top_n=2):
    # Select the top N entries from df1
    df1top_entries = df1.head(df1top_n)
    
    # Select the bottom N entries from df2
    df2top_entries = df2.head(df2top_n)
    
    # Concatenate the selected parts
    merged_df = pd.concat([df1top_entries, df2top_entries], ignore_index=True)
    
    return merged_df

In [449]:
mix = final_reccomended(cosine_reccomendation ,recommendation_svd)

mix

Book Title  \
0                                        Animal Farm   
1                                    Brave New World   
2  Slaughterhouse Five or the Children's Crusade:...   
3                                   The Smoke Jumper   
4  Speaker for the Dead (Ender Wiggins Saga (Pape...   

                                              Author  
0                                      George Orwell  
1                                      Aldous Huxley  
2                                      Kurt Vonnegut  
3  Book-Title
The Smoke Jumper    Nicholas Evans
...  
4  Book-Title
Speaker for the Dead (Ender Wiggins...